# xView

## Dataset
[Armory xView](https://armory-public-data.s3.us-east-2.amazonaws.com/xview/xview.tar.gz)
`HASH: 72c81c118b252c5d9539075760660eb2222811b9bce7c609f594284d785e04e5`

## Model

## Attack
[Armory Attack](https://github.com/twosixlabs/armory/blob/3fd07b4b5e57368f171d940e9601a2016fcc532e/armory/art_experimental/attacks/sweep.py)

In [ ]:
%%bash
# Execute this cell if you are running this notebook in a remote
# jupyter environment. This process may take some time.

IN_COLAB=`python -c "import google.colab"`

if [[ $IN_COLAB -lt 1 ]]; then
  echo "Running setup for Google Colab..."
  git clone https://github.com/twosixlabs/armory.git /armory-repo
  pushd /armory-repo
    pip install --upgrade pip
    pip install ".[pytorch]"
  popd
fi


In [ ]:
# Handle numpy runtime error in Google Colab:
#  https://numpy.org/devdocs/user/troubleshooting-importerror.html#c-api-incompatibility
!pip install numpy==1.23.0 --force
!echo "Please restart the runtime to continue (ctrl + m)..."

### Loading the Scenario
To load the scenario, we use Armory's `get()` function in `armory.scenarios.main`. The filepath used below is an example, and you'll receive the specific path logged to console after invoking `armory run`.

Calling `load()` will load the pieces (model, dataset, attack, etc.) necessary to run the scenario.

In [1]:
# When launched interactively, using --interactive, the scenario config will
# be copied to a time-stamped sub-directory of `/armory/tmp/`.
# Example:
#    >>> # To run, inside of a notebook:
#    >>>     from armory.scenarios.main import get as get_scenario
#    >>>     scenario = get_scenario("/armory/tmp/2022-11-09T130708.219154/interactive-config.json").load()
#    >>>     scenario.evaluate()

import json
from pathlib import Path
from pprint import pprint

from armory.scenarios.main import get as get_scenario

scenario_config = "/armory-repo/scenario_configs/eval1-4/xview/xview_frcnn_sweep_patch_size.json"

# json_config = json.loads(Path(scenario_config).read_text())
# pprint(json_config)

scenario = get_scenario(scenario_config).load()

2023-06-13 20:15:28  0s INFO     armory.delayed_imports:<module>:7 Importing and configuring torch, tensorflow, and art, if available. This may take some time.
2023-06-13 20:15:34  6s INFO     armory.delayed_imports:<module>:30 Setting tf.config.experimental.set_memory_growth to True on all GPUs


2023-06-13 20:15:37  9s ERROR    armory.scenarios.main:_scenario_setup:42 eval_id not in config. Inserting current timestamp 1686687337.947591
2023-06-13 20:15:37  9s INFO     armory.scenarios.main:_scenario_setup:50 armory outputs and logs will be written to /armory/outputs/1686687337.947591
2023-06-13 20:15:38 10s INFO     armory.data.utils:maybe_download_weights_from_s3:49 xview_model_state_dict_epoch_99_loss_0p67 not found in Armory `saved_model_dir`. Attempting to pull weights from S3
2023-06-13 20:15:38 10s INFO     armory.data.utils:download_file_from_s3:130 downloading S3 data file armory-public-data/model-weights/xview_model_state_dict_epoch_99_loss_0p67


/usr/local/lib/python3.10/dist-packages/torchvision/models/_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=FasterRCNN_ResNet50_FPN_Weights.COCO_V1`. You can also use `weights=FasterRCNN_ResNet50_FPN_Weights.DEFAULT` to get the most up-to-date weights.
  warnings.warn(msg)
Downloading: "https://download.pytorch.org/models/fasterrcnn_resnet50_fpn_coco-258fb6c6.pth" to /root/.cache/torch/hub/checkpoints/fasterrcnn_resnet50_fpn_coco-258fb6c6.pth
100%|██████████| 160M/160M [00:00<00:00, 304MB/s]


2023-06-13 20:15:52 24s INFO     armory.scenarios.scenario:load_dataset:254 Loading test dataset xview...
2023-06-13 20:15:52 24s INFO     armory.data.utils:download_verify_dataset_cache:251 Attempting download_verigy_dataset_cache with dataset_dir
2023-06-13 20:15:52 24s INFO     armory.data.utils:download_verify_dataset_cache:282 Downloading dataset: xview...
2023-06-13 20:17:35 2m6s INFO     armory.data.utils:download_requests:195 downloaded /armory/datasets/cache/xview_cached_1.0.1.tar.gz from https://armory-public-data.s3.us-east-2.amazonaws.com/xview/xview_cached_1.0.1.tar.gz
2023-06-13 20:17:35 2m6s INFO     armory.data.utils:download_verify_dataset_cache:299 Verifying sha256 hash of download...
2023-06-13 20:17:39 2m10s INFO     armory.data.utils:download_verify_dataset_cache:315 Extracting .tfrecord files from download...


# Evaluation

Evaluation is normally started using `scenario.evaluate()`, however, below we will illustrate how to iteratively walk through that process and export artifacts.

In [ ]:
from tqdm import tqdm


# Update Attack params
# scenario.config["attack"]["kwargs"]["max_iter"] = 5
scenario.load_attack()


for _ in tqdm(range(len(scenario.test_dataset)), desc="Evaluation"):
  scenario.next()
  if not scenario.skip_benign:
    scenario.run_benign()
    try:
      scenario.sample_exporter.export(scenario.x[0], f"benign_batch_{scenario.i}", with_boxes=False)
      if scenario.y[0] != None and scenario.y_pred[0] != None:
        scenario.sample_exporter.export(
          scenario.x[0],
          f"benign_batch_{scenario.i}_bbox",
          y=scenario.y[0],
          y_pred=scenario.y_pred[0],
          with_boxes=True
        )
    except:
      pass
  if not scenario.skip_attack:
    scenario.run_attack()
    try:
      scenario.sample_exporter.export( scenario.x_adv[0], f"adversarial_batch_{scenario.i}", with_boxes=False)
      if scenario.y[0] != None or scenario.y_pred_adv[0] != None:
        scenario.sample_exporter.export(
          scenario.x_adv[0],
          f"adversarial_batch_{scenario.i}_bbox",
          y=scenario.y[0],
          y_pred=scenario.y_pred_adv[0],
          with_boxes=True
        )
    except:
      pass


scenario.hub.set_context(stage="finished")
scenario.finalize_results()

Evaluation:   0%|          | 0/19277 [00:00<?, ?it/s]

PGD - Iterations:   0%|          | 0/5 [00:00<?, ?it/s]

2023-06-12 23:15:11 2h41m53s INFO     armory.art_experimental.attacks.sweep:generate:121 Failure with kwargs {} and generate_kwargs {'patch_height': 60, 'patch_width': 60}


PGD - Iterations:   0%|          | 0/5 [00:00<?, ?it/s]

2023-06-12 23:15:12 2h41m54s INFO     armory.art_experimental.attacks.sweep:generate:121 Failure with kwargs {} and generate_kwargs {'patch_height': 90, 'patch_width': 90}


...

PGD - Iterations:   0%|          | 0/5 [00:00<?, ?it/s]

2023-06-12 23:25:20 2h52m INFO     armory.art_experimental.attacks.sweep:generate:121 Failure with kwargs {} and generate_kwargs {'patch_height': 60, 'patch_width': 60}


PGD - Iterations:   0%|          | 0/5 [00:00<?, ?it/s]

Evaluation:   1%|          | 125/19277 [10:10<25:59:41,  4.89s/it]


KeyboardInterrupt: ignored

In [ ]:
results_dict = scenario.prepare_results()

print(results_dict["results"])

scenario.save()

In [ ]:
import tarfile
import os

with tarfile.open("scenario_output.tar.gz", "w:gz") as tar:
    tar.add("/armory", arcname=os.path.basename("/armory"))